In [1]:
from tqdm.notebook import tqdm
import jieba
import tiktoken
from transformers import LlamaTokenizerFast
import numpy as np
import pandas as pd
import seaborn as sns
from matplotlib import pyplot as plt
%config InlineBackend.figure_format = 'retina'
plt.rcParams['font.family'] = 'serif'
plt.rcParams['mathtext.fontset'] = 'cm'
plt.rcParams['figure.dpi'] = 120
plt.rcParams['legend.fontsize'] = "medium"
plt.rcParams['axes.labelsize'] = 'large'


ENCODER_DICT = {
    "gpt-4": tiktoken.encoding_for_model("gpt-4"),
    "llama": LlamaTokenizerFast.from_pretrained("hf-internal-testing/llama-tokenizer"),
}


In [2]:
flores_dev_df = pd.read_csv(
    "flores200/flores200_dataset/flores200_dev.tsv",
    sep="\t",
    index_col=None,
)
flores_devtest_df = pd.read_csv(
    "flores200/flores200_dataset/flores200_devtest.tsv",
    sep="\t",
    index_col=None,
)
flores_df = pd.concat([flores_dev_df, flores_devtest_df]).reset_index(drop=True)
flores_df.dropna(axis=0, inplace=True)
flores_df.head(1)

Acehnese (Arabic script)  \
0  يق أورو سنين، اوق علمون دري فکولتس کدوکترن يون...   

                             Acehnese (Latin script)  \
0  Bak uroe Senin, awak ilmuwan dari Fakultas Ked...   

                                 Mesopotamian Arabic  \
0  يوم الأثنين، أعلن علماء من كلية الطب بجامعة ست...   

                                Ta’izzi-Adeni Arabic  \
0  بيوم الاثنين، أعلن علماء من حق كلية الطب بجامع...   

                                     Tunisian Arabic  \
0  يوم الاثنين، أعلن علماء من كلية الطب بجامعة ست...   

                                           Afrikaans  \
0  Op Maandag het wetenskaplikes vanaf die Stanfo...   

                              South Levantine Arabic  \
0  في يوم الإثنين، العلماء من كلية الطب في جامعة ...   

                                                Akan  \
0  Dwoada no, abɔdeɛ mu nimdefoɔ a wɔfiri Stanfor...   

                                             Amharic  \
0  ሰኞ እለት፣ በስታንፎርድ ዩኒቨርሲቲ የህክምና ትምህርት ቤት ህዋሶችን በአ...   

                              North Levantine Arabic  ...  \
0  أعلن علما من كلية الطب بجامعة ستانفورد يوم الت...  ...   

                                               Waray  \
0  Dida han Lunes, iginpasabot han mga sayantista...   

                                               Wolof  \
0  Ci Altine gi, xeltukat yi nekk Daara ju kawe j...   

                                               Xhosa  \
0  NgoMvulo, iinzululwazi ezivela eStandford Univ...   

                                     Eastern Yiddish  \
0  מאנטאג, האבן וויסנשאפטליכער פון סטענפארד אוניו...   

                                              Yoruba  \
0  Àwọn onímọ̀ ìjìnlẹ̀ sáyẹ̀nsì láti ilé ìkẹ́ẹ̀kọ...   

                                         Yue Chinese  \
0  週一，來自史丹福大學醫學院的科學家宣布發明了一種新的診症工具，可以對細胞進行分類：一種可以用...   

                                Chinese (Simplified)  \
0  周一，斯坦福大学医学院的科学家宣布，他们发明了一种可以将细胞按类型分类的新型诊断工具：一种可...   

                               Chinese (Traditional)  \
0  史丹佛大學醫學院的科學家於週一宣布發明一項新型診斷工具，可依類型將細胞分類：這是一種細小的可...   

                                      Standard Malay  \
0  Pada hari Isnin, Saintis daripada Sekolah Peru...   

                                                Zulu  
0  NgoMsombuluko, usosayensi wase-Stanford Univer...  

[1 rows x 204 columns]

In [15]:
flores_df["Chinese (Simplified)"]

0       周一，斯坦福大学医学院的科学家宣布，他们发明了一种可以将细胞按类型分类的新型诊断工具：一种可...
1       主要研究人员表示，这可以让低收入国家/地区的患者尽早发现癌症、肺结核、艾滋病和疟疾。在这些国...
2       当地时间上午 9:30 左右 (UTC 0230)，JAS 39C 鹰狮战斗机撞上跑道并发生...
3                 涉事飞行员是空军中队长迪罗里·帕塔维 (Dilokrit Pattavee)。
4                                当地媒体报道，一辆机场消防车在响应火警时翻了车。
                              ...                        
2004                     这些地区人口稀少，一般不存在光污染的问题，你也能欣赏到璀璨星空。
2005                 与西方人习惯的工作文化相比，日本人的工作文化中等级制度更明显，更加正式。
2006                        西装是标准的商务着装，同事们用彼此的姓氏或职称来互相称呼。
2007                       和谐的职场氛围至关重要，强调团队的努力，而不是表扬个人成就。
2008                   员工在做任何决定时都必须得到上级的批准，并需要无条件服从上级的指示。
Name: Chinese (Simplified), Length: 2008, dtype: object

In [14]:
for l, b in flores_df.map(lambda x: " " not in x).any().items():
    if b: print(l)

South Azerbaijani
Standard Tibetan
Dzongkha
Japanese
Kashmiri (Devanagari script)
Khmer
Lao
Lombard
Minangkabau (Arabic script)
Burmese
Shan
Thai
Tamasheq (Tifinagh script)
Yue Chinese
Chinese (Simplified)
Chinese (Traditional)


In [37]:
tokens_df_dict = dict()
# Load or compute the number of tokens in each text of flores-200 for each model
for model_name in ["gpt-4", "llama"]:
    try:
        tokens_df_dict[model_name] = pd.read_csv(
            f"flores_{model_name}_tokens.tsv", sep="\t", index_col=None
        )
    except FileNotFoundError:
        tokens_df_dict[model_name] = flores_df.map(
            lambda x: len(ENCODER_DICT[model_name].encode(x))
        )
        tokens_df_dict[model_name].to_csv(
            f"flores_{model_name}_tokens.tsv", index=False, sep="\t"
        )
# Transform the dictionary into a single long-form dataframe
token_info_list = []
for model_name in ["gpt-4", "llama"]:
    for language in tokens_df_dict[model_name].columns:
        for token_count in tokens_df_dict[model_name][language].values:
            token_info_list.append({"Model": model_name, "Tokens": token_count, "Language": language})
tokens_df = pd.DataFrame(token_info_list)

In [63]:
# Sort the languages by the average number of tokens
sorted_langs = tokens_df.groupby("Language")["Tokens"].mean().sort_values().index.to_list()
tokens_df.sort_values(by="Language", key=lambda langs: [sorted_langs.index(l) for l in langs], inplace=True)
tokens_df.reset_index(inplace=True)

In [125]:
n_groups = 4
lang_groups = [sorted_langs[i*len(sorted_langs)//n_groups:(i+1)*len(sorted_langs)//n_groups] for i in range(n_groups)]
# flores_tokens_df.loc[:, lang_groups[0]]

In [126]:
fig, axs = plt.subplots(1, n_groups, figsize=(10, 24), constrained_layout=True, dpi=300)
for ax, group in zip(axs, lang_groups):
    df = tokens_df[tokens_df["Language"].isin(group)]
    # sns.boxplot(fliersize=1,
    # sns.barplot(
    sns.violinplot(split=True,
        data=df, x="Tokens", y="Language", hue="Model",
        hue_order=["gpt-4", "llama"], palette=["C2", "C0"],
        orient="h", linewidth=0.25, ax=ax,
    )
    ax.legend().remove()
    ax.set_ylabel("")
    labels = ax.get_yticklabels()
    ax.set_yticks([])
    xlim = ax.get_xlim()
    for i, lang_label in enumerate(labels):
        lang_name = lang_label.get_text()
        if "(" in lang_name:
            lang_name = lang_name.replace("(", "\n(", 1)
        elif " " in lang_name:
            lang_name = lang_name.replace(" ", "\n", 1)
        ax.text(0.9*xlim[1], i, lang_name,
                va="center" if "\n" in lang_name else "bottom", ha="right", fontsize=8)
# ax.invert_xaxis()

plt.show()

/home/agustin/Documents/other_projects/tokens-thorugh-lang/langtoken_env/lib/python3.10/site-packages/seaborn/_oldcore.py:1498: FutureWarning: is_categorical_dtype is deprecated and will be removed in a future version. Use isinstance(dtype, CategoricalDtype) instead
  if pd.api.types.is_categorical_dtype(vector):
/home/agustin/Documents/other_projects/tokens-thorugh-lang/langtoken_env/lib/python3.10/site-packages/seaborn/_oldcore.py:1498: FutureWarning: is_categorical_dtype is deprecated and will be removed in a future version. Use isinstance(dtype, CategoricalDtype) instead
  if pd.api.types.is_categorical_dtype(vector):
/home/agustin/Documents/other_projects/tokens-thorugh-lang/langtoken_env/lib/python3.10/site-packages/seaborn/_oldcore.py:1498: FutureWarning: is_categorical_dtype is deprecated and will be removed in a future version. Use isinstance(dtype, CategoricalDtype) instead
  if pd.api.types.is_categorical_dtype(vector):
/home/agustin/Documents/other_projects/tokens-thorugh-l